In [1]:
import gc
import pandas as pd
import seaborn as sns
import numpy as np
import plotly.express as px
from tqdm import tqdm
gc.collect()

basepath = 'C:/Users/avasquez/Desktop/kaggle/novozymes-enzyme-stability-prediction/'
train_path = basepath + 'train.csv'
train_path_updates = basepath + 'train_updates_20220929.csv'
test_path = basepath + 'test.csv'

In [2]:
##read test set and drop na/nan values if they exist
test_df = pd.read_csv(test_path, index_col="seq_id")
test_df.dropna(inplace=True, axis=0)

##read and fix train set
train_df = pd.read_csv("train.csv", index_col="seq_id")
df_train_updates = pd.read_csv(train_path_updates, index_col="seq_id")

all_features_nan = df_train_updates.isnull().all("columns")

drop_indices = df_train_updates[all_features_nan].index
train_df = train_df.drop(index=drop_indices)

swap_ph_tm_indices = df_train_updates[~all_features_nan].index
train_df.loc[swap_ph_tm_indices, ["pH", "tm"]] = df_train_updates.loc[swap_ph_tm_indices, ["pH", "tm"]]
train_df.dropna(inplace=True, axis=0)

In [3]:
%%time

print('Column names: ', list(train_df))
print('Number Train Samples: ', train_df['protein_sequence'].size)
print('Number Test Samples: ', test_df['protein_sequence'].size)
print('Protein_sequence Num Unique Vals: ', train_df['protein_sequence'].unique().size)

Column names:  ['protein_sequence', 'pH', 'data_source', 'tm']
Number Train Samples:  27727
Number Test Samples:  2413
Protein_sequence Num Unique Vals:  26879
CPU times: total: 15.6 ms
Wall time: 24.9 ms


In [4]:
import plotly.express as px
hist = px.histogram(train_df, x='tm', title="Histogram of Melting Temperature")
hist.show()

In [5]:
train_df = train_df[(train_df['tm'] >= 20) & (train_df['tm'] <= 100)]
hist = px.histogram(train_df, x='tm', title="Histogram of Melting Temperature without Outliers")
hist.show()

In [6]:
hist = px.histogram(train_df, x='pH', title="Histogram of pH")
hist.show()

In [7]:
train_df = train_df[(train_df['pH'] <= 8.5)]
hist = px.histogram(train_df, x='pH', title="Histogram of pH without Outliers")
hist.show()

In [8]:
%%time
'''
Encoding the protein sequences appropriately to minimize data loss is a particulary challenging
problem. I thought that the simplest approach was to establish a letter count and a total sequence
count. This approach is simple, but leaves out the important feature of sequence order.
'''
def count_sequence(sequence):
    s_dict = {'A': [], 'B': [], 'C': [], 'D': [], 'E': [], 'F': [], 'G': [], 'H': [],
              'I': [], 'J': [], 'K': [], 'L': [], 'M': [], 'N': [], 'O': [], 'P': [],
              'Q': [], 'R': [], 'S': [], 'T': [], 'U': [], 'V': [], 'W': [], 'X': [],
              'Y': [], 'Z': []}
    
    for idx, letter in enumerate(sequence):
        s_dict[letter].append(letter)
        
    letter_cnt_list = []
    for key in s_dict.keys():
        letter_cnt_list.append(len(s_dict[key]))
    letter_cnt_list.append(idx)
    return np.array(letter_cnt_list)

##count train set sequence data and append to dataframe
rows = []
seq_data_train = np.empty([train_df['pH'].values.shape[0], 27])
for sequence in tqdm(train_df['protein_sequence'], desc='Counting Train Sequence'):
    rows.append(np.array(count_sequence(sequence)))
seq_data_train = np.array(rows)
    
col_names = ['A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L',
             'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X',
             'Y', 'Z', 'seq_len']

print('Train Sequence Data Shape: ', seq_data_train.shape)
df_train = pd.DataFrame(seq_data_train, columns=col_names)
df_train['pH'] = train_df['pH'].values
df_train['tm'] = train_df['tm'].values
print(df_train.tail())

##count test set sequence data and append to dataframe
rows = []
seq_data_test = np.empty([test_df['pH'].values.shape[0], 27])
for sequence in tqdm(test_df['protein_sequence'], desc='Counting Test Sequence'):
    rows.append(np.array(count_sequence(sequence)))
seq_data_test = np.array(rows)
    
print('\nTest Sequence Data Shape: ', seq_data_test.shape)
df_test = pd.DataFrame(seq_data_test, columns=col_names)
df_test['pH'] = test_df['pH'].values
print(df_test.tail())

Counting Train Sequence: 100%|████████████████████████████████████████████████| 27593/27593 [00:01<00:00, 26800.76it/s]


Train Sequence Data Shape:  (27593, 27)
        A  B   C   D   E   F   G   H   I  J  ...   T  U   V   W  X   Y  Z  \
27588  33  0  12  38  31  18  51  15  21  0  ...  18  0  42  13  0  18  0   
27589  37  0   5  21  29  22  27  22  30  0  ...  26  0  34   5  0  14  0   
27590  13  0   1   7   7   7  11   2   6  0  ...   6  0   7   4  0   4  0   
27591  47  0   5  34  36  23  52  11  34  0  ...  32  0  48   3  0  18  0   
27592  34  0   5  15  32  26  24  21  31  0  ...  29  0  38  18  0  29  0   

       seq_len   pH    tm  
27588      548  7.0  51.8  
27589      468  7.0  37.2  
27590      127  7.0  64.6  
27591      592  7.0  50.7  
27592      536  7.0  37.6  

[5 rows x 29 columns]


Counting Test Sequence: 100%|███████████████████████████████████████████████████| 2413/2413 [00:00<00:00, 51512.97it/s]


Test Sequence Data Shape:  (2413, 27)
       A  B  C   D  E   F   G  H  I  J  ...   S  T  U   V  W  X  Y  Z  \
2408  21  0  4  15  7  10  19  0  7  0  ...  18  8  0  13  6  0  6  0   
2409  21  0  4  15  7  10  19  0  6  0  ...  18  8  0  13  6  0  6  0   
2410  21  0  4  15  7  10  19  0  6  0  ...  18  8  0  13  6  0  6  0   
2411  21  0  4  15  7  10  19  0  6  0  ...  18  8  0  13  6  0  6  0   
2412  21  0  4  15  7  10  19  0  6  0  ...  18  8  0  13  7  0  6  0   

      seq_len  pH  
2408      220   8  
2409      220   8  
2410      220   8  
2411      220   8  
2412      220   8  

[5 rows x 28 columns]
CPU times: total: 1.17 s
Wall time: 1.1 s


In [9]:
%%time

##remove unwanted columns from train and test data
y_train = train_df['tm'].values
X_train = df_train.values
X_test = df_test.values
X_train = df_train.drop(columns=['tm'], axis=1)
# X_test = df_test.drop(columns=['data_source'], axis=1)
print('Train set num samples: ', len(X_train))
print('Test set num samples: ', len(X_test))

# ##combine X_train and X_test for encoding
# data_tmp = pd.concat([X_train, X_test])
# one_hot = pd.get_dummies(data_tmp['protein_sequence'])
# data_tmp = data_tmp.drop('protein_sequence', axis=1)
# data_tmp = data_tmp.join(one_hot)
# data_tmp = data_tmp.astype(np.float64)
# print('Dataset num features: ', len(list(data_tmp)))

# ##separate back into train and test sets
# X_test = data_tmp.values[27593:]
# X_train = data_tmp.values[:27593]
# print('\nRe-split X_train Shape: ', X_train.shape)
# print('Re-split X_test Shape: ', X_test.shape)

Train set num samples:  27593
Test set num samples:  2413
CPU times: total: 0 ns
Wall time: 5.01 ms


In [10]:
%%time
from sklearn.preprocessing import StandardScaler
##scale X_train
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)

##scale
scaler = StandardScaler()
X_test = scaler.fit_transform(X_test)

print(X_train)

[[ 0.30199699  0.         -0.56112326 ...  0.         -0.28686389
   0.1451055 ]
 [-0.21868361  0.         -0.65808822 ...  0.         -0.41764467
   0.1451055 ]
 [ 0.45513834  0.          0.21459643 ...  0.          0.08407796
   0.1451055 ]
 ...
 [-0.67810766  0.         -0.56112326 ...  0.         -0.79334217
   0.1451055 ]
 [ 0.36325353  0.         -0.17326341 ...  0.          0.31234986
   0.1451055 ]
 [-0.03491399  0.         -0.17326341 ...  0.          0.17919125
   0.1451055 ]]
CPU times: total: 46.9 ms
Wall time: 46.8 ms


In [11]:
%%time

##data dimension reduction
import umap
reducer = umap.UMAP(verbose=1, n_jobs=-1, target_metric='l2', n_components=16)
reduced = reducer.fit(X_train, y_train)

##metric learning
test_embedding = reducer.transform(X_test)

##sanity check
print('Train Embedding Shape: ', reducer.embedding_.shape)
print('Test Embedding Shape: ', test_embedding.shape)

UMAP(n_components=16, target_metric='l2', verbose=1)
Wed Nov  9 12:31:08 2022 Construct fuzzy simplicial set
Wed Nov  9 12:31:08 2022 Finding Nearest Neighbors
Wed Nov  9 12:31:08 2022 Building RP forest with 13 trees
Wed Nov  9 12:31:08 2022 NN descent for 15 iterations
	 1  /  15
	 2  /  15
	 3  /  15
	 4  /  15
	Stopping threshold met -- exiting after 4 iterations
Wed Nov  9 12:31:21 2022 Finished Nearest Neighbor Search
Wed Nov  9 12:31:27 2022 Construct embedding


Epochs completed:   0%|            0/200 [00:00]

Wed Nov  9 12:31:39 2022 Finished embedding
Wed Nov  9 12:31:40 2022 Worst tree score: 0.63168195
Wed Nov  9 12:31:40 2022 Mean tree score: 0.63719896
Wed Nov  9 12:31:40 2022 Best tree score: 0.64462001
Wed Nov  9 12:31:43 2022 Forward diversification reduced edges from 413895 to 176604
Wed Nov  9 12:31:45 2022 Reverse diversification reduced edges from 176604 to 176604


C:\Users\avasquez\Anaconda3\envs\machineLearning\lib\site-packages\scipy\sparse\_index.py:125: SparseEfficiencyWarning:

Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.



Wed Nov  9 12:31:47 2022 Degree pruning reduced edges from 200130 to 199945
Wed Nov  9 12:31:47 2022 Resorting data and graph based on tree order
Wed Nov  9 12:31:47 2022 Building and compiling search function


Epochs completed:   0%|            0/100 [00:00]

Train Embedding Shape:  (27593, 16)
Test Embedding Shape:  (2413, 16)
CPU times: total: 3min 43s
Wall time: 55.4 s


In [12]:
##sanity check
embedding_df = pd.DataFrame()
embedding_df['e1'] = reduced.embedding_[:,0]
embedding_df['e2'] = reduced.embedding_[:,1] 
embedding_df['target'] = y_train
plot = px.scatter(embedding_df, x="e1", y="e2", color='target', 
                  title="UMAP Feature Space of Two Dimensions")
plot.show()

It appears that using dimension reduction teqniques offer little help. As seen from the above feature space plot from metric learning with UMAP, clusterring is not a viable option, or atleast not with this algorithm.

In [13]:
%%time

from sklearn.model_selection import cross_val_score
from sklearn.tree import DecisionTreeRegressor
dt_regressor = DecisionTreeRegressor(random_state=0, max_depth=20)
# dtr_scores = cross_val_score(dt_regressor, reduced.embedding_, y_train, 
dtr_scores = cross_val_score(dt_regressor, X_train, y_train, 
                             scoring='neg_root_mean_squared_error', 
                             cv=10, verbose=1, n_jobs=-1)

print('Cross Validation Scores: ', dtr_scores)
print('Cross Validation Mean Score: ', sum(dtr_scores)/len(dtr_scores))
print('Cross Validation Stdev Score: ', np.std(dtr_scores))
print('\n')

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 16 concurrent workers.


Cross Validation Scores:  [-11.29746747 -10.65851022 -10.35385979 -12.00115801 -12.95628689
 -11.47203499 -12.7128103  -11.20155443 -12.03964123 -11.63281111]
Cross Validation Mean Score:  -11.632613443764923
Cross Validation Stdev Score:  0.7828436336427208


CPU times: total: 15.6 ms
Wall time: 1.54 s


[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    1.3s finished


In [14]:
%%time

from sklearn.linear_model import LinearRegression

linear_reg = LinearRegression(n_jobs=-1)
lr_scores = cross_val_score(linear_reg, X_train, y_train, cv=10, scoring='neg_root_mean_squared_error',
                              verbose=1, n_jobs=-1)

print('Cross Validation Scores: ', lr_scores)
print('Cross Validation Mean Score: ', sum(lr_scores)/len(lr_scores))
print('Cross Validation Stdev Score: ', np.std(lr_scores))
print('\n')

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 16 concurrent workers.


Cross Validation Scores:  [-10.24458946  -9.0459459  -11.12870857 -11.82040367 -12.88376204
 -11.14954001 -12.41565278 -10.06095693 -10.87272256 -11.19508832]
Cross Validation Mean Score:  -11.0817370266852
Cross Validation Stdev Score:  1.0734452246993815


CPU times: total: 15.6 ms
Wall time: 497 ms


[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    0.3s finished


In [15]:
%%time

from sklearn.ensemble import RandomForestRegressor

rf = RandomForestRegressor(max_depth=20, n_estimators=200, n_jobs=-1, warm_start=True)
rf_scores = cross_val_score(rf, X_train, y_train, cv=10, scoring='neg_root_mean_squared_error',
                              verbose=1, n_jobs=-1)

print('Cross Validation Scores: ', rf_scores)
print('Cross Validation Mean Score: ', sum(rf_scores)/len(rf_scores))
print('Cross Validation Stdev Score: ', np.std(rf_scores))
print('\n')

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 16 concurrent workers.


Cross Validation Scores:  [-8.20015587 -7.24114709 -7.648256   -8.64871644 -9.98094115 -8.14824704
 -8.75737387 -7.99446093 -9.25298164 -8.18889749]
Cross Validation Mean Score:  -8.406117751748573
Cross Validation Stdev Score:  0.7507700589129761


CPU times: total: 46.9 ms
Wall time: 36.8 s


[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   36.5s finished


In [16]:
%%time

##split a small validation set for sanity
from sklearn.model_selection import train_test_split
X_tr, X_val, y_tr, y_val = train_test_split(X_train, y_train, test_size=0.05, random_state=42)

##train random forest regressor
rf = RandomForestRegressor(max_depth=20, n_estimators=200, n_jobs=-1, warm_start=True).fit(X_tr, y_tr)
##evaluate using mse
from sklearn.metrics import mean_squared_error
y_pred = rf.predict(X_val) 
print('Random Forest MSE: ', mean_squared_error(y_val, y_pred, squared=False))

Random Forest MSE:  7.9264786317621665
CPU times: total: 1min 5s
Wall time: 4.42 s


In [17]:
%%time

##get test predictions
preds = rf.predict(X_test)
print('Prediction Shape: ', preds.shape)
print('Last prediction: ', preds[-1])

Prediction Shape:  (2413,)
Last prediction:  49.21100205815894
CPU times: total: 31.2 ms
Wall time: 26.4 ms


In [18]:
##write to csv
preds_df = pd.DataFrame(test_df.index.values, columns=['seq_id'])
preds_df['tm'] = preds 
preds_df.to_csv(basepath + 'vasquez_submission.csv', index = False)